# IBM Applied Data Science Capstone Course by Coursera

### Opening a cafe in Delhi, India
>Delhi is a big city and has a ton of options when it comes to café places. For anyone new to the café business it will be difficult survive as there is a lot of competition in this market.

>If an entrepreneur wants to open a café in Delhi at what places should he/she open his/her business so that they face the least competition. There are lots of neighborhoods in Delhi we will have to conduct analysis to see which area can be considered for opening a café. We can leverage the foursquare data by calling data of all the café situated in the specific neighborhoods.


## Importing neighborhood data and performing data wrangling:

In [1]:
import pandas as pd
import numpy as np

In [2]:
df=pd.read_csv("datasets_512081_944688_delhi_dataSet (1).csv")
df.head()

Unnamed: 0           Borough  Neighborhood   latitude  longitude
0           0  North West Delhi  Adarsh Nagar  28.614192  77.071541
1           1  North West Delhi   Ashok Vihar  28.699453  77.184826
2           2  North West Delhi       Azadpur  28.707657  77.175547
3           3  North West Delhi        Bawana  28.799660  77.032885
4           4  North West Delhi     Begum Pur        NaN        NaN

In [3]:
df=df.drop(columns=['Unnamed: 0'])

In [4]:
df=df.drop(columns=['Borough'])

In [5]:
df=df.dropna()

In [6]:
df


Neighborhood   latitude  longitude
0      Adarsh Nagar  28.614192  77.071541
1       Ashok Vihar  28.699453  77.184826
2           Azadpur  28.707657  77.175547
3            Bawana  28.799660  77.032885
5             Dhaka  39.031714 -90.261223
..              ...        ...        ...
178  Rajouri Garden  28.642152  77.116060
179   Shivaji Place  28.651657  77.121703
181     Tilak Nagar  28.639650  77.094039
183     Vikas Nagar  28.644009  77.054470
184       Vikaspuri  28.638419  77.070836

[163 rows x 3 columns]

## Getting the map of Delhi with the neighborhood coordinates imposed on it 

In [7]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

In [8]:
# get the coordinates of banglore
address = 'delhi ,India'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of delhi , india {}, {}.'.format(latitude, longitude))

The geograpical coordinate of delhi , india 28.6517178, 77.2219388.


In [9]:
map_ = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng,neighborhood in zip(df['latitude'], df['longitude'],df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_)  
    
map_

## Calling foursquare API to get venue data:

In [10]:
CLIENT_ID = 'D30WNCL2F50I0ODTY213G4PPG1PWYVDHKI25VUZLNJKBN4VP' # your Foursquare ID
CLIENT_SECRET = 'NHD2FMAYP3ROYTGTFCKVTC3R05DIPIIKSD55D0ZL4VMSKQZO' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: D30WNCL2F50I0ODTY213G4PPG1PWYVDHKI25VUZLNJKBN4VP
CLIENT_SECRET:NHD2FMAYP3ROYTGTFCKVTC3R05DIPIIKSD55D0ZL4VMSKQZO


In [17]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(df['latitude'], df['longitude'], df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

## 	Analyzing the venue data and preparing data for clustering:

In [18]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df.head()


(6711, 7)


Neighborhood   Latitude  Longitude        VenueName  VenueLatitude  \
0  Adarsh Nagar  28.614192  77.071541    Shree Maakhan      28.625825   
1  Adarsh Nagar  28.614192  77.071541  Cafe Coffee Day      28.622388   
2  Adarsh Nagar  28.614192  77.071541   Domino's Pizza      28.630000   
3  Adarsh Nagar  28.614192  77.071541  Cafe Coffee Day      28.629794   
4  Adarsh Nagar  28.614192  77.071541           Subway      28.630026   

   VenueLongitude      VenueCategory  
0       77.068608  Indian Restaurant  
1       77.088353               Café  
2       77.080000        Pizza Place  
3       77.079771        Coffee Shop  
4       77.079541     Sandwich Place

In [19]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                        
Adarsh Nagar              14         14         14             14   
Alaknanda                 57         57         57             57   
Anand Vihar               35         35         35             35   
Ashok Nagar                1          1          1              1   
Ashok Vihar               32         32         32             32   
Azadpur                   29         29         29             29   
Babarpur                   7          7          7              7   
Badarpur                   4          4          4              4   
Bali Nagar                43         43         43             43   
Bara Hindu Rao            88         88         88             88   
Barakhamba Road          100        100        100            100   
Bawana                     3          3          3              3   
Brij Puri                  8          8          8              8   
Chanakyapuri              74         74         74             74   
Chandni Chowk            200        200        200            200   
Chawri Bazaar             81         81         81             81   
Chhattarpur               27         27         27             27   
Chittaranjan Park         91         91         91             91   
Civil Lines               33         33         33             33   
Connaught Place          100        100        100            100   
Dariba Kalan              58         58         58             58   
Daryaganj                 30         30         30             30   
Dayanand Colony          100        100        100            100   
Defence Colony            99         99         99             99   
Delhi Cantonment           9          9          9              9   
Dhaka                      1          1          1              1   
Dhaula Kuan               78         78         78             78   
Dilshad Garden             7          7          7              7   
East Vinod Nagar          11         11         11             11   
East of Kailash          100        100        100            100   
Fateh Nagar               41         41         41             41   
Friends Colony            58         58         58             58   
Gandhi Nagar               1          1          1              1   
Gautampuri                 4          4          4              4   
Geeta Colony              17         17         17             17   
Ghitorni                  13         13         13             13   
Gole Market              100        100        100            100   
Golf Links               100        100        100            100   
Govindpuri                 1          1          1              1   
Greater Kailash           83         83         83             83   
Green Park               100        100        100            100   
Gulmohar Park            100        100        100            100   
Hauz Khas                100        100        100            100   
Hauz Khas Village        100        100        100            100   
INA Colony                64         64         64             64   
Inderpuri                 11         11         11             11   
Jahangirpuri               6          6          6              6   
Jaitpur                    6          6          6              6   
Janakpuri                 24         24         24             24   
Jangpura                  85         85         85             85   
Jasola                    15         15         15             15   
Jhandewalan               66         66         66             66   
Jhilmil Colony            17         17         17             17   
Jor Bagh                  58         58         58             58   
Kabir Nagar                5          5          5              5   
Kailash Colony           100        100        100            100   
Kalkaji           

In [20]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 220 uniques categories.


In [21]:
venues_df.groupby('Neighborhood').count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                        
Adarsh Nagar              14         14         14             14   
Alaknanda                 57         57         57             57   
Anand Vihar               35         35         35             35   
Ashok Nagar                1          1          1              1   
Ashok Vihar               32         32         32             32   
Azadpur                   29         29         29             29   
Babarpur                   7          7          7              7   
Badarpur                   4          4          4              4   
Bali Nagar                43         43         43             43   
Bara Hindu Rao            88         88         88             88   
Barakhamba Road          100        100        100            100   
Bawana                     3          3          3              3   
Brij Puri                  8          8          8              8   
Chanakyapuri              74         74         74             74   
Chandni Chowk            200        200        200            200   
Chawri Bazaar             81         81         81             81   
Chhattarpur               27         27         27             27   
Chittaranjan Park         91         91         91             91   
Civil Lines               33         33         33             33   
Connaught Place          100        100        100            100   
Dariba Kalan              58         58         58             58   
Daryaganj                 30         30         30             30   
Dayanand Colony          100        100        100            100   
Defence Colony            99         99         99             99   
Delhi Cantonment           9          9          9              9   
Dhaka                      1          1          1              1   
Dhaula Kuan               78         78         78             78   
Dilshad Garden             7          7          7              7   
East Vinod Nagar          11         11         11             11   
East of Kailash          100        100        100            100   
Fateh Nagar               41         41         41             41   
Friends Colony            58         58         58             58   
Gandhi Nagar               1          1          1              1   
Gautampuri                 4          4          4              4   
Geeta Colony              17         17         17             17   
Ghitorni                  13         13         13             13   
Gole Market              100        100        100            100   
Golf Links               100        100        100            100   
Govindpuri                 1          1          1              1   
Greater Kailash           83         83         83             83   
Green Park               100        100        100            100   
Gulmohar Park            100        100        100            100   
Hauz Khas                100        100        100            100   
Hauz Khas Village        100        100        100            100   
INA Colony                64         64         64             64   
Inderpuri                 11         11         11             11   
Jahangirpuri               6          6          6              6   
Jaitpur                    6          6          6              6   
Janakpuri                 24         24         24             24   
Jangpura                  85         85         85             85   
Jasola                    15         15         15             15   
Jhandewalan               66         66         66             66   
Jhilmil Colony            17         17         17             17   
Jor Bagh                  58         58         58             58   
Kabir Nagar                5          5          5              5   
Kailash Colony           100        100        100            100   
Kalkaji           

In [22]:
# one hot encoding
df_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
df_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [df_onehot.columns[-1]] + list(df_onehot.columns[:-1])
df_onehot = df_onehot[fixed_columns]

print(df_onehot.shape)
df_onehot.head()

(6711, 221)


Neighborhoods  ATM  Accessories Store  Afghan Restaurant  Airport  \
0  Adarsh Nagar    0                  0                  0        0   
1  Adarsh Nagar    0                  0                  0        0   
2  Adarsh Nagar    0                  0                  0        0   
3  Adarsh Nagar    0                  0                  0        0   
4  Adarsh Nagar    0                  0                  0        0   

   Airport Food Court  Airport Service  Airport Terminal  American Restaurant  \
0                   0                0                 0                    0   
1                   0                0                 0                    0   
2                   0                0                 0                    0   
3                   0                0                 0                    0   
4                   0                0                 0                    0   

   Antique Shop  Arcade  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0       0            0           0                    0   
1             0       0            0           0                    0   
2             0       0            0           0                    0   
3             0       0            0           0                    0   
4             0       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  BBQ Joint  \
0                 0                   0                      0          0   
1                 0                   0                      0          0   
2                 0                   0                      0          0   
3                 0                   0                      0          0   
4                 0                   0                      0          0   

   Bagel Shop  Bakery  Bank  Bar  Bed & Breakfast  Beer Garden  \
0           0       0     0    0                0            0   
1           0       0     0    0                0            0   
2           0       0     0    0                0            0   
3           0       0     0    0                0            0   
4           0       0     0    0                0            0   

   Bengali Restaurant  Big Box Store  Bike Shop  Bistro  Boat or Ferry  \
0                   0              0          0       0              0   
1                   0              0          0       0              0   
2                   0              0          0       0              0   
3                   0              0          0       0              0   
4                   0              0          0       0              0   

   Bookstore  Boutique  Bowling Alley  Breakfast Spot  Brewery  Buffet  \
0          0         0              0               0        0       0   
1          0         0              0               0        0       0   
2          0         0              0               0        0       0   
3          0         0              0               0        0       0   
4          0         0              0               0        0       0   

   Building  Burger Joint  Burmese Restaurant  Bus Station  Business Service  \
0         0             0                   0            0                 0   
1         0             0                   0            0                 0   
2         0             0                   0            0                 0   
3         0             0                   0            0                 0   
4         0             0                   0            0                 0   

   Cafeteria  Café  Campground  Castle  Chinese Restaurant  Chocolate Shop  \
0          0     0           0       0                   0               0   
1          0     1           0       0                   0               0   
2          0     0           0       0                   0               0   
3          0     0           0       0                   0               0   
4          0     0          

In [23]:
df_onehot.groupby(["Neighborhoods"]).sum()

ATM  Accessories Store  Afghan Restaurant  Airport  \
Neighborhoods                                                            
Adarsh Nagar          0                  0                  0        0   
Alaknanda             0                  0                  0        0   
Anand Vihar           0                  0                  0        0   
Ashok Nagar           0                  0                  0        0   
Ashok Vihar           0                  0                  0        0   
Azadpur               0                  0                  0        0   
Babarpur              0                  0                  0        0   
Badarpur              0                  0                  0        0   
Bali Nagar            0                  0                  0        0   
Bara Hindu Rao        0                  0                  0        0   
Barakhamba Road       0                  0                  0        0   
Bawana                1                  0                  0        0   
Brij Puri             4                  0                  0        0   
Chanakyapuri          0                  0                  0        0   
Chandni Chowk         0                  0                  0        0   
Chawri Bazaar         0                  0                  0        0   
Chhattarpur           0                  0                  0        0   
Chittaranjan Park     0                  0                  0        0   
Civil Lines           0                  0                  0        0   
Connaught Place       0                  0                  0        0   
Dariba Kalan          0                  0                  0        0   
Daryaganj             0                  0                  0        0   
Dayanand Colony       0                  0                  0        0   
Defence Colony        0                  0                  1        0   
Delhi Cantonment      0                  0                  0        0   
Dhaka                 0                  0                  0        0   
Dhaula Kuan           0                  0                  0        0   
Dilshad Garden        0                  0                  0        0   
East Vinod Nagar      0                  0                  0        0   
East of Kailash       0                  0                  0        0   
Fateh Nagar           0                  0                  0        0   
Friends Colony        0                  0                  0        0   
Gandhi Nagar          0                  0                  0        0   
Gautampuri            0                  0                  0        0   
Geeta Colony          0                  0                  0        0   
Ghitorni              0                  0                  0        0   
Gole Market           0                  0                  0        0   
Golf Links            0                  0                  0        0   
Govindpuri            0                  0                  0        0   
Greater Kailash       0                  0                  0        0   
Green Park            0                  0                  0        0   
Gulmohar Park         0                  0                  0        0   
Hauz Khas             0                  0                  0        0   
Hauz Khas Village     0                  0                  0        0   
INA Colony            0                  0                  0        0   
Inderpuri             0                  0                  0        0   
Jahangirpuri          0                  0                  0        0   
Jaitpur               3                  0                  0        0   
Janakpuri             0                  0                  0        0   
Jangpura              0                  0                  1        0   
Jasola                0                  0                  0        0   
Jhandewalan           0                  0                  0        0   
Jhilmil Colony        0 

In [24]:

df_grouped = df_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(df_grouped.shape)
df_grouped

(154, 221)


Neighborhoods       ATM  Accessories Store  Afghan Restaurant  \
0          Adarsh Nagar  0.000000           0.000000           0.000000   
1             Alaknanda  0.000000           0.000000           0.000000   
2           Anand Vihar  0.000000           0.000000           0.000000   
3           Ashok Nagar  0.000000           0.000000           0.000000   
4           Ashok Vihar  0.000000           0.000000           0.000000   
5               Azadpur  0.000000           0.000000           0.000000   
6              Babarpur  0.000000           0.000000           0.000000   
7              Badarpur  0.000000           0.000000           0.000000   
8            Bali Nagar  0.000000           0.000000           0.000000   
9        Bara Hindu Rao  0.000000           0.000000           0.000000   
10      Barakhamba Road  0.000000           0.000000           0.000000   
11               Bawana  0.333333           0.000000           0.000000   
12            Brij Puri  0.500000           0.000000           0.000000   
13         Chanakyapuri  0.000000           0.000000           0.000000   
14        Chandni Chowk  0.000000           0.000000           0.000000   
15        Chawri Bazaar  0.000000           0.000000           0.000000   
16          Chhattarpur  0.000000           0.000000           0.000000   
17    Chittaranjan Park  0.000000           0.000000           0.000000   
18          Civil Lines  0.000000           0.000000           0.000000   
19      Connaught Place  0.000000           0.000000           0.000000   
20         Dariba Kalan  0.000000           0.000000           0.000000   
21            Daryaganj  0.000000           0.000000           0.000000   
22      Dayanand Colony  0.000000           0.000000           0.000000   
23       Defence Colony  0.000000           0.000000           0.010101   
24     Delhi Cantonment  0.000000           0.000000           0.000000   
25                Dhaka  0.000000           0.000000           0.000000   
26          Dhaula Kuan  0.000000           0.000000           0.000000   
27       Dilshad Garden  0.000000           0.000000           0.000000   
28     East Vinod Nagar  0.000000           0.000000           0.000000   
29      East of Kailash  0.000000           0.000000           0.000000   
30          Fateh Nagar  0.000000           0.000000           0.000000   
31       Friends Colony  0.000000           0.000000           0.000000   
32         Gandhi Nagar  0.000000           0.000000           0.000000   
33           Gautampuri  0.000000           0.000000           0.000000   
34         Geeta Colony  0.000000           0.000000           0.000000   
35             Ghitorni  0.000000           0.000000           0.000000   
36          Gole Market  0.000000           0.000000           0.000000   
37           Golf Links  0.000000           0.000000           0.000000   
38           Govindpuri  0.000000           0.000000           0.000000   
39      Greater Kailash  0.000000           0.000000           0.000000   
40           Green Park  0.000000           0.000000           0.000000   
41        Gulmohar Park  0.000000           0.000000           0.000000   
42            Hauz Khas  0.000000           0.000000           0.000000   
43    Hauz Khas Village  0.000000           0.000000           0.000000   
44           INA Colony  0.000000           0.000000           0.000000   
45            Inderpuri  0.000000           0.000000           0.000000   
46         Jahangirpuri  0.000000           0.000000           0.000000   
47              Jaitpur  0.500000           0.000000           0.000000   
48            Janakpuri  0.000000           0.000000           0.000000   
49             Jangpura  0.000000           0.000000           0.011765   
50               Jasola  0.000000           0.000000           0.000000   
51          Jhandewalan  0.000000           0.000000           0.000000   
52       Jhilmil Colony  0.000000  

In [25]:
len(df_grouped[df_grouped["Café"] > 0])

106

In [26]:
df_cafe = df_grouped[["Neighborhoods","Café"]]

In [27]:
df_cafe.head()

Neighborhoods      Café
0  Adarsh Nagar  0.071429
1     Alaknanda  0.052632
2   Anand Vihar  0.085714
3   Ashok Nagar  0.000000
4   Ashok Vihar  0.062500

## Performing K-MEAN clustering:

In [28]:
kclusters = 3

df_clustering = df_cafe.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(df_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 2, 0, 2, 2, 1, 0, 2])

In [29]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
df_merged = df_cafe.copy()

# add clustering labels
df_merged["Cluster Labels"] = kmeans.labels_

In [30]:
df_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
df_merged.head()

Neighborhood      Café  Cluster Labels
0  Adarsh Nagar  0.071429               0
1     Alaknanda  0.052632               0
2   Anand Vihar  0.085714               0
3   Ashok Nagar  0.000000               2
4   Ashok Vihar  0.062500               0

In [31]:
# merge delhi_grouped with delhi_data to add latitude/longitude for each neighborhood
df_merged = df_merged.join(df.set_index("Neighborhood"), on="Neighborhood")

print(df_merged.shape)
df_merged.head() # check the last columns!

(163, 5)


Neighborhood      Café  Cluster Labels   latitude  longitude
0  Adarsh Nagar  0.071429               0  28.614192  77.071541
1     Alaknanda  0.052632               0  28.529336  77.251632
2   Anand Vihar  0.085714               0  28.625691  77.101941
3   Ashok Nagar  0.000000               2  39.031714 -90.261223
4   Ashok Vihar  0.062500               0  28.699453  77.184826

In [32]:
# sort the results by Cluster Labels
print(df_merged.shape)
df_merged.sort_values(["Cluster Labels"], inplace=True)
df_merged

(163, 5)


Neighborhood      Café  Cluster Labels   latitude  longitude
0          Adarsh Nagar  0.071429               0  28.614192  77.071541
101           Paharganj  0.070000               0  28.641926  77.221750
101           Paharganj  0.070000               0  28.641926  77.221750
100               Okhla  0.133333               0  28.563662  77.289055
99      Nizamuddin West  0.045455               0  28.588365  77.244955
98   New Friends Colony  0.085714               0  28.567101  77.269764
97         Netaji Nagar  0.051724               0  28.573534  77.186359
95          Nehru Place  0.043011               0  28.549257  77.252952
93           Neeti Bagh  0.080460               0  28.559251  77.216166
87              Munirka  0.114754               0  28.554886  77.171084
86           Moti Nagar  0.060606               0  28.657859  77.142429
85            Moti Bagh  0.095238               0  28.577879  77.174180
102               Palam  0.080000               0  28.567173  77.134032
83             Mehrauli  0.045455               0  28.521826  77.178323
152           Wazirabad  0.060000               0  28.433762  77.087757
76        Maharani Bagh  0.111111               0  28.572001  77.263372
75          Lodi Colony  0.070423               0  28.590702  77.220921
73         Lajpat Nagar  0.080000               0  28.565462  77.245627
71        Krishna Nagar  0.080000               0  28.563702  77.193410
68   Kishangarh Village  0.052632               0  28.519428  77.166535
67          Kirti Nagar  0.117647               0  28.652368  77.149642
66          Kirby Place  0.111111               0  28.611741  77.128527
64       Khirki Village  0.090000               0  28.529885  77.218077
62          Khan Market  0.050000               0  28.600135  77.226491
59           Karol Bagh  0.047619               0  28.652998  77.189023
81          Mayur Vihar  0.105263               0  28.613107  77.295722
105         Patel Nagar  0.095238               0  28.659809  77.156957
106          Patparganj  0.045455               0  28.611592  77.290564
107          Pitam Pura  0.041667               0  28.703268  77.132250
151         Vivek Vihar  0.045455               0  28.669164  77.312267
150       Vishwas Nagar  0.071429               0  28.664470  77.291741
149           Vikaspuri  0.080000               0  28.638419  77.070836
146        Vasant Vihar  0.083333               0  28.560691  77.160791
145         Vasant Kunj  0.087719               0  28.529249  77.154134
142         Tilak Nagar  0.085106               0  28.639650  77.094039
141        Sriniwaspuri  0.072917               0  28.565220  77.254704
140     South Extension  0.084337               0  28.568566  77.220568
138           Siri Fort  0.080000               0  28.552146  77.224698
137       Shivaji Place  0.072727               0  28.651657  77.121703
134       Shalimar Bagh  0.055556               0  28.717453  77.150867
133        Shakti Nagar  0.128205               0  28.679790  77.194914
133        Shakti Nagar  0.128205               0  28.679790  77.194914
132           Shakarpur  0.062500               0  28.629489  77.281061
131         Shahpur Jat  0.091837               0  28.548330  77.214104
129   Sarvodaya Enclave  0.110000               0  28.537478  77.202089
125     Sarai Kale Khan  0.078947               0  28.586626  77.256228
124          Sant Nagar  0.085714               0  28.646418  77.091188
122               Saket  0.080000               0  28.524411  77.213725
120  Safdarjung Enclave  0.070000               0  28.565642  77.193438
115  Rama Krishna Puram  0.107143               0  28.575561  77.172303
114      Rajouri Garden  0.068966               0  28.642152  77.116060
110         Preet Vihar  0.060606               0  28.637753  77.295175
109        Pratap Nagar  0.057143               0  28.666718  77.198897
108      Pragati Maidan  0.075000               0  28.623459  77.242512
57          Kamla Nagar  0.128205               0  

## VISUALIZING THE CLUSTERS

In [33]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df_merged['latitude'], df_merged['longitude'], df_merged['Neighborhood'], df_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-3],
        fill=True,
        fill_color=rainbow[cluster-3],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [35]:
map_clusters.save('map_clusters.html')

## NOW WE OBSERVE THIS MAP AND THE CLUSTERS

In [36]:
df_merged.loc[df_merged['Cluster Labels'] == 0]

Neighborhood      Café  Cluster Labels   latitude  longitude
0          Adarsh Nagar  0.071429               0  28.614192  77.071541
101           Paharganj  0.070000               0  28.641926  77.221750
101           Paharganj  0.070000               0  28.641926  77.221750
100               Okhla  0.133333               0  28.563662  77.289055
99      Nizamuddin West  0.045455               0  28.588365  77.244955
98   New Friends Colony  0.085714               0  28.567101  77.269764
97         Netaji Nagar  0.051724               0  28.573534  77.186359
95          Nehru Place  0.043011               0  28.549257  77.252952
93           Neeti Bagh  0.080460               0  28.559251  77.216166
87              Munirka  0.114754               0  28.554886  77.171084
86           Moti Nagar  0.060606               0  28.657859  77.142429
85            Moti Bagh  0.095238               0  28.577879  77.174180
102               Palam  0.080000               0  28.567173  77.134032
83             Mehrauli  0.045455               0  28.521826  77.178323
152           Wazirabad  0.060000               0  28.433762  77.087757
76        Maharani Bagh  0.111111               0  28.572001  77.263372
75          Lodi Colony  0.070423               0  28.590702  77.220921
73         Lajpat Nagar  0.080000               0  28.565462  77.245627
71        Krishna Nagar  0.080000               0  28.563702  77.193410
68   Kishangarh Village  0.052632               0  28.519428  77.166535
67          Kirti Nagar  0.117647               0  28.652368  77.149642
66          Kirby Place  0.111111               0  28.611741  77.128527
64       Khirki Village  0.090000               0  28.529885  77.218077
62          Khan Market  0.050000               0  28.600135  77.226491
59           Karol Bagh  0.047619               0  28.652998  77.189023
81          Mayur Vihar  0.105263               0  28.613107  77.295722
105         Patel Nagar  0.095238               0  28.659809  77.156957
106          Patparganj  0.045455               0  28.611592  77.290564
107          Pitam Pura  0.041667               0  28.703268  77.132250
151         Vivek Vihar  0.045455               0  28.669164  77.312267
150       Vishwas Nagar  0.071429               0  28.664470  77.291741
149           Vikaspuri  0.080000               0  28.638419  77.070836
146        Vasant Vihar  0.083333               0  28.560691  77.160791
145         Vasant Kunj  0.087719               0  28.529249  77.154134
142         Tilak Nagar  0.085106               0  28.639650  77.094039
141        Sriniwaspuri  0.072917               0  28.565220  77.254704
140     South Extension  0.084337               0  28.568566  77.220568
138           Siri Fort  0.080000               0  28.552146  77.224698
137       Shivaji Place  0.072727               0  28.651657  77.121703
134       Shalimar Bagh  0.055556               0  28.717453  77.150867
133        Shakti Nagar  0.128205               0  28.679790  77.194914
133        Shakti Nagar  0.128205               0  28.679790  77.194914
132           Shakarpur  0.062500               0  28.629489  77.281061
131         Shahpur Jat  0.091837               0  28.548330  77.214104
129   Sarvodaya Enclave  0.110000               0  28.537478  77.202089
125     Sarai Kale Khan  0.078947               0  28.586626  77.256228
124          Sant Nagar  0.085714               0  28.646418  77.091188
122               Saket  0.080000               0  28.524411  77.213725
120  Safdarjung Enclave  0.070000               0  28.565642  77.193438
115  Rama Krishna Puram  0.107143               0  28.575561  77.172303
114      Rajouri Garden  0.068966               0  28.642152  77.116060
110         Preet Vihar  0.060606               0  28.637753  77.295175
109        Pratap Nagar  0.057143               0  28.666718  77.198897
108      Pragati Maidan  0.075000               0  28.623459  77.242512
57          Kamla Nagar  0.128205               0  

In [37]:
df_merged.loc[df_merged['Cluster Labels'] == 1]

Neighborhood      Café  Cluster Labels   latitude  longitude
103      Pandav Nagar  0.176471               1  28.650127  77.153278
96        Nehru Vihar  0.166667               1  28.710745  77.221174
33         Gautampuri  0.250000               1  28.511570  77.302623
28   East Vinod Nagar  0.181818               1  28.622766  77.307504
127      Sarita Vihar  0.266667               1  28.533478  77.293523
26        Dhaula Kuan  0.153846               1  28.591891  77.161703
26        Dhaula Kuan  0.153846               1  28.591891  77.161703
143          Timarpur  0.235294               1  28.701263  77.218680
50             Jasola  0.266667               1  28.542233  77.294386
148       Vikas Nagar  0.333333               1  28.644009  77.054470
46       Jahangirpuri  0.166667               1  28.725972  77.162658
7            Badarpur  0.250000               1  28.503638  77.301976

In [38]:
df_merged.loc[df_merged['Cluster Labels'] == 2]

Neighborhood      Café  Cluster Labels   latitude  longitude
3           Ashok Nagar  0.000000               2  39.031714 -90.261223
18          Civil Lines  0.030303               2  28.676857  77.225056
121         Sainik Farm  0.000000               2  28.503746  77.216073
123        Sangam Vihar  0.000000               2  28.497702  77.239174
123        Sangam Vihar  0.000000               2  28.497702  77.239174
147  Vasundhara Enclave  0.000000               2  28.601726  77.321122
5               Azadpur  0.000000               2  28.707657  77.175547
144         Tughlaqabad  0.000000               2  28.511192  77.262327
126       Sarai Rohilla  0.000000               2  28.667873  77.190267
130            Shahdara  0.000000               2  28.677304  77.290347
6              Babarpur  0.000000               2  28.687430  77.279755
139         Sonia Vihar  0.000000               2  28.719926  77.248182
9        Bara Hindu Rao  0.000000               2  28.659518  77.205010
9        Bara Hindu Rao  0.000000               2  28.659518  77.205010
136        Shastri Park  0.000000               2  28.668434  77.250530
128      Sarojini Nagar  0.032258               2  28.574158  77.195370
135       Shastri Nagar  0.000000               2  39.031714 -90.261223
135       Shastri Nagar  0.000000               2  39.031714 -90.261223
128      Sarojini Nagar  0.032258               2  28.574158  77.195370
11               Bawana  0.000000               2  28.799660  77.032885
119      Roshanara Bagh  0.034483               2  28.673718  77.199320
130            Shahdara  0.000000               2  28.677304  77.290347
12            Brij Puri  0.000000               2  28.702509  77.273777
118             Rithala  0.000000               2  28.720806  77.107181
54          Kabir Nagar  0.000000               2  28.692670  77.283544
116            Rangpuri  0.000000               2  28.540007  77.119775
79              Mandoli  0.000000               2  28.680604  77.294690
77           Mahipalpur  0.000000               2  28.544485  77.125691
74          Laxmi Nagar  0.040000               2  28.630309  77.277563
72          Lahori Gate  0.025974               2  28.656841  77.218534
44           INA Colony  0.031250               2  28.579472  77.212451
70              Kotwali  0.019608               2  28.658598  77.231084
69        Kohat Enclave  0.027778               2  28.698041  77.140539
80              Maujpur  0.000000               2  28.692013  77.279651
45            Inderpuri  0.000000               2  28.628684  77.147098
65        Kingsway Camp  0.018182               2  28.614262  77.201555
63              Khanpur  0.000000               2  28.512798  77.232395
61         Keshav Puram  0.000000               2  28.688926  77.161683
60        Kashmiri Gate  0.000000               2  28.669977  77.232059
58               Karala  0.000000               2  28.735140  77.032511
51          Jhandewalan  0.015152               2  28.644336  77.199927
56              Kalkaji  0.000000               2  39.031714 -90.261223
47              Jaitpur  0.000000               2  28.500477  77.316192
82           Meera Bagh  0.000000               2  28.658844  77.090848
38           Govindpuri  0.000000               2  39.031714 -90.261223
84           Model Town  0.000000               2  39.031714 -90.261223
20         Dariba Kalan  0.000000               2  28.654602  77.233379
113             Rajokri  0.036364               2  28.513170  77.110766
112        Punjabi Bagh  0.030303               2  28.668945  77.132461
111         Pul Bangash  0.000000               2  39.031714 -90.261223
21            Daryaganj  0.000000               2  28.646090  77.243048
24     Delhi Cantonment  0.000000               2  28.583536  77.125985
25                Dhaka  0.000000               2  39.031714 -90.261223
104       Paschim Vihar  0.000000               2  28.669578  77.095956
27       Dilshad Garden  0.000000               2  

## OBSERVATION
### It can be seen that the cluster 1 has the highest concentration of cafes so it is not suitable for oppening a new cafe as there is a lot of competition, on the other hand cluster 2 has the least concentration of cafes making it the suitable choice for opening a new cafe in these neighborhoods. while cluster 0 shows moderate level of competition as it has moderate concentration of cafes 